<div style="background-color: #e6e6fa; padding: 10px;">
    <h1>Introduction</h1>
</div>

<div style="display: flex; justify-content: space-between; align-items: flex-start;">
    <div style="padding: 10px; width: 70%;">
        <p>This notebook delves into the comprehensive global inflation dataset hosted on <a href="https://www.kaggle.com/datasets/sazidthe1/global-inflation-data/data">Kaggle</a>, originally derived from the World Bank's <a href="https://data.worldbank.org/">website</a>. Featuring annual average inflation rates for 197 countries from 1980 to the current day, the dataset provides a rich basis for analysis.</p>
        <p>The examination kicks off by spotlighting edge cases, initially highlighting countries with exceptionally high inflation, followed by those with negative inflation rates. This exploration sets the stage for a deeper dive into the nuances of global inflation trends.</p>
        <p>To facilitate a clear and insightful visualization, country-specific inflation rates are depicted through line graphs. For enhanced readability and to avoid skewing the data representation, inflation rates above 100 are uniformly capped at "100+". It is critical to acknowledge that while these values are represented as 100+, they can range dramatically, from just above 100 to well over 1000 in the most extreme instances.</p>
    </div>
    <div style="padding: 10px; width: 30%; text-align: right;">
        <img src="https://github.com/ocarhaci/images/blob/main/inflation.png?raw=true" alt="Inflation trends" style="width: 100%; height: auto;">
    </div>
</div>
<div style="display: flex; justify-content: space-between; align-items: flex-start;">
    <div style="padding: 10px; width: 100%;">
                <p>The analysis is structured into two main sections:</p>
        <ul>
            <li><strong>Edge Case Plots:</strong> This section showcases countries with inflation rates higher than 100 or lower than 0.</li>
            <li><strong>Inflation per Country:</strong> Here, the inflation trends of 197 countries are graphically represented.</li>
        </ul>
        <h3 style="color: green;"><strong><em>Your engagement with this notebook is highly valued. If you find it informative, kindly consider upvoting.</em></strong></h3>
        <p>The dataframe is imported from the dataset below, alongside the definition of several helper functions for use in subsequent sections. Expand the next cell to review the code.</p>
    </div>
</div>


In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from IPython.display import display, HTML

df = pd.read_csv('/kaggle/input/global-inflation-data/global_inflation_data.csv')

def plot_inflation_graphs(df, num_graphs):
    # Ensure the number of graphs does not exceed the number of countries in the DataFrame
    num_countries = min(num_graphs, df.shape[0])

    # Setup the subplot grid
    ncols = 2  # Number of columns in the subplot grid
    nrows = int(num_countries / ncols) + (num_countries % ncols > 0)  # Calculate rows needed

    fig, axs = plt.subplots(nrows, ncols, figsize=(15, nrows * 4))
    fig.subplots_adjust(hspace=0.4, wspace=0.4)  # Adjust spacing between plots
    
    for i in range(num_countries):
        row = i // ncols
        col = i % ncols
        
        # Select data for the current country
        country_data = df.iloc[i, 2:]  # Exclude country_name and indicator columns
        years = country_data.index.astype(int)
        
        # Ensure the data is numeric and replace non-numeric values with NaN
        values = pd.to_numeric(country_data.values, errors='coerce')
        
        # Cap values at 120 for those greater than 100
        modified_values = np.where(values > 100, 120, values)
        
        # Plotting on the respective subplot
        ax = axs[row, col] if nrows > 1 else axs[col] if nrows == 1 else axs
        ax.plot(years, modified_values, marker='o', linestyle='-')
        ax.set_title(df.iloc[i, 0])
        ax.set_xlabel("Year")
        ax.set_ylabel("Inflation")
        ax.grid(True)
        ax.tick_params(labelrotation=45)
        
        # Adjust y-ticks to exclude values beyond the cap
        y_ticks = ax.get_yticks()
        y_ticks = y_ticks[y_ticks <= 120]  # Keep y-ticks up to and including the cap
        y_tick_labels = [f"{y:.0f}" if y < 120 else "100+" for y in y_ticks]
        ax.set_yticks(y_ticks)
        ax.set_yticklabels(y_tick_labels)

    # If the number of countries is odd, hide the last subplot if it's unused
    if num_countries % ncols:
        axs[-1, -1].axis('off')

    plt.tight_layout()
    plt.show()

    
def find_high_inflation_countries(df):
    high_inflation_countries = {}  # Dictionary to store results
    
    # Exclude non-numeric columns (e.g., country names) from the comparison
    numeric_df = df.select_dtypes(include=[np.number])
    
    for index, row in numeric_df.iterrows():
        country_name = df.loc[index, 'country_name']  # Get the country name from the original DataFrame
        high_inflation_years = row[row > 100].index.tolist()  # Now, this comparison is safe
        
        if high_inflation_years:
            # Assuming years are direct column names, adjust if needed
            high_inflation_countries[country_name] = high_inflation_years

    return high_inflation_countries


def display_side_by_side(df, columns):    
    # Convert the input data into a DataFrame if it's not already one
    results_df = pd.DataFrame(list(df.items()), columns=columns)
    
    # Split the DataFrame into two halves
    midpoint = len(results_df) // 2
    left_df = results_df.iloc[:midpoint]
    right_df = results_df.iloc[midpoint:]
    
    # Convert both halves to HTML
    left_html = left_df.to_html(index=False)
    right_html = right_df.to_html(index=False)
    
    # Add styling to headers in both halves
    left_html = left_html.replace('<th>', '<th style="font-weight: bold; text-decoration: underline;">')
    right_html = right_html.replace('<th>', '<th style="font-weight: bold; text-decoration: underline;">')
    
    # Combine the two halves into a single HTML structure, using divs for side-by-side display
    combined_html = f'''
    <div style="display: flex; justify-content: space-between;">
        <div style="width: 49%; margin-right: 1%;">{left_html}</div>
        <div style="width: 49%; margin-left: 1%;">{right_html}</div>
    </div>
    '''
    
    # Display the combined HTML
    display(HTML(combined_html))

def find_negative_inflation_countries(df):
    negative_inflation_countries = {}  # Dictionary to store results
    
    # Exclude non-numeric columns (e.g., country names) from the comparison
    numeric_df = df.select_dtypes(include=[np.number])
    
    for index, row in numeric_df.iterrows():
        country_name = df.loc[index, 'country_name']  # Get the country name from the original DataFrame
        high_inflation_years = row[row < 0].index.tolist()  # Now, this comparison is safe
        
        if high_inflation_years:
            # Assuming years are direct column names, adjust if needed
            negative_inflation_countries[country_name] = high_inflation_years

    return negative_inflation_countries

<div style="background-color: #e6e6fa; padding: 10px;">
    <h1>Edge Case Plots</h1>
</div>

<div style="padding: 10px;">
    <h3 style="text-decoration: underline;">Countries with inflation higher than 100:</h3>
</div>

In [2]:
high_inflation_countries = find_high_inflation_countries(df)
display_side_by_side(high_inflation_countries, ['Country', 'Years with Inflation > 100'])


<div style="padding: 10px;">
    <h3 style="text-decoration: underline;">Countries with negative inflation:</h3>
</div>

In [3]:
negative_inflation_countries = find_negative_inflation_countries(df)
display_side_by_side(negative_inflation_countries, ['Country', 'Years with Negative Inflation'])


<div style="background-color: #e6e6fa; padding: 10px;">
    <h1>Inflation per Country</h1>
</div>

In [4]:
plot_inflation_graphs(df, num_graphs=197) 


<div style="background-color: #e6e6fa; padding: 10px;">
    <h1>Thanks for reading.</h1>
</div>